In [1]:
import pandas as pd
import numpy as np
from datetime import date
from collections import Counter
from numpy import loadtxt
from pyspark.sql import SparkSession 
from pyspark.sql.types import *
from pyspark.ml.feature import Bucketizer
from pyspark.sql import DataFrame
from typing import Iterable
from pyspark.sql import functions 
from pyspark.sql.functions import *
from pyspark.sql import Row
from pyspark.sql.functions import pandas_udf
from pyspark.sql.functions import PandasUDFType
from pyspark.sql.types import DoubleType, StructField
from pyspark.sql.window import Window

In [2]:
#read data from history file
#global_temp_db = spark.conf.get("spark.sql.globalTempDatabase")
#train_df=spark.sql("select * from {0}".format(global_temp_db + ".a_historical_test_pyspark_banu"))

train_df=sqlContext.read.format('csv').options(header='true', inferSchema='true', dateFormat='M/d/yyyy HH:mm').load('/FileStore/tables/MVP3_testing_Historical_20_26_27.csv') 
test_df=sqlContext.read.format('csv').options(header='true', inferSchema='true', dateFormat='M/d/yyyy HH:mm').load('/FileStore/tables/MVP3_testing_Future_20_26_27_June.csv') 

train_df = train_df.withColumn('flight_boarding_time',unix_timestamp(train_df['flight_boarding_time'],'M/d/yyyy HH:mm').cast("timestamp"))
test_df = test_df.withColumn('flight_boarding_time',unix_timestamp(test_df['flight_boarding_time'],'M/d/yyyy HH:mm').cast("timestamp"))

train_df  = train_df.withColumn("split", lit(1))
test_df  = test_df.withColumn("split", lit(0))
test_df.Meal = np.nan

In [3]:
#this will yield non deterministic results, bypass this while validating
train_df = train_df.drop_duplicates(['flight_number', 'flight_boarding_pt','flight_boarding_time','itemcategory','dishsubcategory','menu_cycle','destination'])

#train_df.createOrReplaceTempView("train_df_table")
#train_df = sqlContext.sql("WITH grp AS (SELECT p.*, ROW_NUMBER() OVER(PARTITION BY p.flight_number, p.flight_boarding_pt,p.flight_boarding_time ,p.itemcategory, p.dishsubcategory , p.menu_cycle , p.destination ORDER BY p.flight_number, p.flight_boarding_pt,p.flight_boarding_time ,p.itemcategory,p.dishsubcategory , p.menu_cycle , p.destination) AS rnk FROM train_df_table p) SELECT * FROM grp  WHERE rnk = 1")   


In [4]:
test_df = test_df.drop_duplicates(['flight_number', 'flight_boarding_pt','flight_boarding_time','itemcategory','dishsubcategory','menu_cycle','destination'])

In [5]:
display(train_df)

flight_number flight_boarding_pt flight_boarding_time menu_cycle destination itemcategory C F M U Africa Americas Asia China Europe Germany Gulf India Indonesia Iran Italy Japan Mauritus Northern Africa Oceania Thailand Adults Children Elders Middle Aged Teenagers year month quarter week day dayofweek Meal dishsubcategory pax_count argentinian asian asian / chinese asian / japanese continental / european german indian indian ocean / mauritian indonesian italian middle eastern middle eastern / gulf middle eastern / iranian north african thai split 1 DXB 2017-08-16T07:45:00.000+0000 A LHR Lunch null 22.0 26.0 null 6.0 1.0 4.0 3.0 19.0 null null 2.0 null null null null 2.0 null 9.0 null 15.0 2.0 11.0 17.0 2.0 2017 8 3 33 16 2 16.0 Poultry 49 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 1 DXB 2017-08-28T07:45:00.000+0000 A LHR Lunch 2.0 15.0 41.0 null 1.0 2.0 6.0 null 24.0 null 3.0 1.0 null null 1.0 null 1.0 null 18.0 null 15.0 2.0 10.0 28.0 2.0 2017 8 3 35 28 0 17.0 Red Meat 58 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 1 DXB 2017-10-05T07:45:00.000+0000 A LHR Lunch null 26.0 31.0 null 1.0 1.0 11.0 null 25.0 2.0 null 4.0 null null 1.0 null 1.0 null 11.0 null 11.0 null 13.0 33.0 null 2017 10 4 40 5 3 20.0 Seafood 57 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 1 DXB 2017-10-10T07:45:00.000+0000 A LHR Lunch null 13.0 33.0 null 4.0 null 4.0 null 25.0 null 1.0 null null null null null null 1.0 10.0 null 8.0 null 12.0 25.0 null 2017 10 4 41 10 1 13.0 Seafood 48 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 1 DXB 2017-11-09T07:45:00.000+0000 B LHR Lunch null 18.0 39.0 null 4.0 3.0 4.0 null 38.0 null 2.0 null null null null null null null 5.0 null 11.0 null 15.0 30.0 null 2017 11 4 45 9 3 29.0 Poultry 57 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 1 DXB 2018-04-12T07:45:00.000+0000 A LHR Lunch null 20.0 31.0 null 5.0 2.0 null null 24.0 null 1.0 1.0 null null null null null null 13.0 4.0 5.0 null 18.0 26.0 1.0 2018 4 2 15 12 3 17.0 Poultry 50 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 DXB 2018-05-12T07:45:00.000+0000 B LHR Lunch 1.0 15.0 32.0 null 5.0 null null null 22.0 null 1.0 null null null null null null 1.0 18.0 1.0 7.0 1.0 15.0 25.0 null 2018 5 2 19 12 5 14.0 Seafood 49 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 2 LHR 2017-05-31T14:15:00.000+0000 B DXB Lunch null 13.0 25.0 null 1.0 1.0 3.0 null 20.0 null 5.0 3.0 null null null null null 1.0 3.0 1.0 8.0 1.0 10.0 16.0 3.0 2017 5 2 22 31 2 13.0 Poultry 40 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 2 LHR 2017-07-22T14:15:00.000+0000 STR DXB Lunch null 18.0 36.0 null null null 17.0 null 22.0 1.0 5.0 2.0 null 1.0 null null null null 6.0 null 10.0 1.0 13.0 26.0 4.0 2017 7 3 29 22 5 21.0 Seafood 54 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 2 LHR 2018-02-02T13:40:00.000+0000 A DXB Lunch null 29.0 38.0 null 2.0 2.0 null null 54.0 null 2.0 3.0 null null 1.0 null null null 2.0 null 15.0 null 24.0 28.0 null 2018 2 1 5 2 4 12.0 Red Meat 66 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 3 DXB 2017-10-16T14:15:00.000+0000 A LHR Lunch null 7.0 27.0 null 1.0 null 1.0 1.0 20.0 null 3.0 4.0 null 1.0 null null null null 3.0 null 8.0 null 9.0 17.0 null 2017 10 4 42 16 0 19.0 Poultry 37 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 3 DXB 2017-12-06T14:25:00.000+0000 FEST2017 LHR Lunch null 13.0 31.0 null null 3.0 1.0 null 28.0 null 1.0 null null null null null null null 10.0 null 7.0 null 5.0 30.0 1.0 2017 12 4 49 6 2 9.0 Seafood 47 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 4 LHR 2017-07-28T20:40:00.000+0000 B DXB Dinner null 15.0 16.0 null 4.0 null 6.0 null 10.0 1.0 7.0 null null null null null null null 3.0 null 6.0 1.0 8.0 10.0 6.0 2017 7 3 30 28 4 12.0 Seafood 40 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 4 LHR 2017-12-15T20:20:00.000+0000 A DXB Dinner null 16.0 23.0 null 1.0 1.0 7.0 null 21.0 null 2.0 2.0 null 1.0 null null null 1.0 2.0 1.0 15.0 1.0 6.0 11.0 6.0 2017 12 4 50 15 4 20.0 Poultry 42 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 4 LHR 2017-12-18T20:20:00.000+0000 A DXB Dinner 2.0 25.0 16.0 null 8.0 3.0 2.0 null 24.0 null 2.0 1.0 null null null null null null 2.0 null 9.0 4.0 8.0 20.0 1.0 2017 12 4 51 18 0 4.0 Seafood 41 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1

In [6]:
train_df.count()

Out[ 21 ]: 36641

In [7]:
test_cols=set(test_df.columns)
train_cols=set(train_df.columns)
combined_cols = sorted(train_cols.union(test_cols))

def addAndorderColumns(df, columnsOrderList):
  columns = []
  for colName in columnsOrderList:
      if colName in df.columns:
          columns.append(colName)
      else:
          columns.append(lit(None).alias(colName))
  return df.select(columns)

test_df_lit = addAndorderColumns(test_df,combined_cols)
train_df_lit = addAndorderColumns(train_df,combined_cols)

combined_df = train_df_lit.union(test_df_lit)
combined_df=combined_df.orderBy(['flight_number', 'flight_boarding_pt', 'flight_boarding_time'], ascending=False)


In [8]:
lagged_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,14,30,60]
part_cols=["flight_number","flight_boarding_pt","itemcategory","dishsubcategory","menu_cycle","destination"]

my_window = Window.partitionBy(part_cols).orderBy('flight_boarding_time')


# get t-i values of 'Meal'
for i in lagged_list:
    
    #combined_df = combined_df.withColumn('prev_Meal', lag("meal",i).over(my_window).alias("meal_"+str(i)))
    combined_df = combined_df.select("*", lag("meal",i).over(my_window).alias("meal"+str(i)))

In [9]:
combined_df.count()

Out[ 25 ]: 37349

In [10]:
display(combined_df)

Adults Africa Americas Asia C Children China Elders Europe F Germany Gulf India Indonesia Iran Italy Japan M Mauritus Meal Middle Aged Northern Africa Oceania Teenagers Thailand U argentinian asian asian / chinese asian / japanese continental / european day dayofweek destination dishsubcategory flight_boarding_pt flight_boarding_time flight_number german indian indian ocean / mauritian indonesian italian itemcategory menu_cycle middle eastern middle eastern / gulf middle eastern / iranian month north african pax_count quarter split thai week year meal1 meal2 meal3 meal4 meal5 meal6 meal7 meal8 meal9 meal10 meal11 meal12 meal13 meal14 meal30 meal60 12.0 null 2.0 12.0 1.0 3.0 null 8.0 22.0 20.0 null 2.0 3.0 null null null 1.0 27.0 null 28.0 25.0 null 6.0 null null null 0 0 0 0 0 1 0 LHR Poultry DXB 2017-05-01T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 49 2 1 0 18 2017 null null null null null null null null null null null null null null null null 8.0 1.0 null 2.0 null null 2.0 12.0 29.0 20.0 null 1.0 4.0 1.0 null null 1.0 28.0 null 25.0 26.0 null 7.0 2.0 null null 0 0 0 0 0 2 1 LHR Poultry DXB 2017-05-02T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 48 2 1 0 18 2017 28.0 null null null null null null null null null null null null null null null 8.0 4.0 3.0 2.0 null 1.0 null 14.0 24.0 14.0 3.0 4.0 null null null null null 36.0 null 20.0 26.0 null 9.0 null null null 0 0 0 0 1 3 2 LHR Poultry DXB 2017-05-03T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 0 0 0 5 0 50 2 1 0 18 2017 25.0 28.0 null null null null null null null null null null null null null null 8.0 null null 3.0 2.0 3.0 null 4.0 12.0 13.0 null 4.0 2.0 null null null null 11.0 null 21.0 11.0 null 5.0 null null null 0 0 0 0 1 4 3 LHR Poultry DXB 2017-05-04T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 0 0 0 5 0 33 2 1 0 18 2017 20.0 25.0 28.0 null null null null null null null null null null null null null 17.0 2.0 2.0 5.0 null null null 9.0 34.0 22.0 null 2.0 7.0 null null null null 36.0 1.0 23.0 31.0 null 5.0 1.0 null null 0 0 0 0 1 7 6 LHR Poultry DXB 2017-05-07T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 0 0 0 5 0 60 2 1 0 18 2017 21.0 20.0 25.0 28.0 null null null null null null null null null null null null 7.0 null 3.0 7.0 null null null 8.0 15.0 11.0 null 1.0 1.0 1.0 null 1.0 null 24.0 null 16.0 20.0 null 4.0 null 1.0 null 0 0 0 0 0 8 0 LHR Poultry DXB 2017-05-08T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 38 2 1 0 19 2017 23.0 21.0 20.0 25.0 28.0 null null null null null null null null null null null 15.0 2.0 2.0 3.0 null null null 15.0 27.0 25.0 null 4.0 6.0 null null 1.0 null 31.0 null 23.0 25.0 1.0 10.0 1.0 null null 0 0 0 0 0 10 2 LHR Poultry DXB 2017-05-10T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 58 2 1 0 19 2017 16.0 23.0 21.0 20.0 25.0 28.0 null null null null null null null null null null 10.0 null 1.0 1.0 null null 1.0 13.0 30.0 21.0 null 2.0 4.0 null null null null 27.0 null 26.0 24.0 1.0 5.0 1.0 3.0 null 0 0 0 0 0 11 3 LHR Poultry DXB 2017-05-11T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 52 2 1 0 19 2017 23.0 16.0 23.0 21.0 20.0 25.0 28.0 null null null null null null null null null 8.0 null 1.0 6.0 null null null 10.0 30.0 11.0 null null 4.0 null null null null 38.0 null 23.0 31.0 null 8.0 null null null 0 0 0 0 0 12 4 LHR Poultry DXB 2017-05-12T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 52 2 1 0 19 2017 26.0 23.0 16.0 23.0 21.0 20.0 25.0 28.0 null null null null null null null null 8.0 null null 1.0 2.0 1.0 null 5.0 22.0 7.0 null null 4.0 1.0 null null null 25.0 null 15.0 19.0 null 5.0 null null null 0 0 0 0 1 13 5 LHR Poultry DXB 2017-05-13T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 0 0 0 5 0 34 2 1 0 19 2017 23.0 26.0 23.0 16.0 23.0 21.0 20.0 25.0 28.0 null null null null null null null 15.0 3.0 2.0 7.0 null null null 5.0 17.0 16.0 1.0 4.0 3.0 null null null null 30.0 null 21.0 26.0 1.0 8.0 null null null 0 0 0 0 0 14 6 LHR Poultry DXB 2017-05-14T14:15:00.000+0000 3 0 0 0 0 0 Lunch B 1 0 0 5 0 47 2 1 0 19 2017 15.0 23.0 26.0 23.0 16.0 23.0 21.0 2

In [11]:
def ewma_udf(df):
    schema = (df.select(['flight_number', 'flight_boarding_pt', 'dishsubcategory','flight_boarding_time','meal' ])
        .schema.add(StructField('exp_smooth', DoubleType())))

    @pandas_udf(schema, PandasUDFType.GROUPED_MAP)
    def ema(pdf):
        pdf['ewm'] = pdf['meal'].ewm(span=15, min_periods=0).mean()
        return pdf

    return df.groupby(['flight_number', 'flight_boarding_pt', 'dishsubcategory']).apply(ema)

temp_ewma = combined_df.select(['flight_number', 'flight_boarding_pt', 'dishsubcategory', 'flight_boarding_time','meal'])

temp_ewma = ewma_udf(temp_ewma)

In [12]:
combined_df = combined_df.join(temp_ewma,  on = ['flight_number', 'flight_boarding_pt', 'dishsubcategory','flight_boarding_time','meal'],how='left')

In [13]:
def holt_winters_second_order_ewma( x, span, beta ):
    N = x.size
    alpha = 2.0 / ( 1 + span )
    s = np.zeros(( N, ))
    b = np.zeros(( N, ))
    s[0] = x[0]
    for i in range( 1, N ):
        s[i] = alpha * x[i] + ( 1 - alpha )*( s[i-1] + b[i-1] )
        b[i] = beta * ( s[i] - s[i-1] ) + ( 1 - beta ) * b[i-1]
    return s    

def holt_winters_second_order_ewma_udf(df):
    schema = (df.select(['flight_number', 'flight_boarding_pt', 'dishsubcategory','flight_boarding_time','meal' ])
        .schema.add(StructField('Doub_exp_smooth', DoubleType())))

    @pandas_udf(schema, PandasUDFType.GROUPED_MAP)
    def ema(pdf):
        pdf['Doub_exp_smooth'] = holt_winters_second_order_ewma(pdf['meal'],span=15, beta=0.3)
        return pdf

    return df.groupby(['flight_number', 'flight_boarding_pt', 'dishsubcategory']).apply(ema)

temp_duble_ewma = combined_df.select(['flight_number', 'flight_boarding_pt', 'dishsubcategory', 'flight_boarding_time','meal'])

temp_duble_ewma = holt_winters_second_order_ewma_udf(temp_duble_ewma)

In [14]:
combined_df = combined_df.join(temp_duble_ewma,  on = ['flight_number', 'flight_boarding_pt', 'dishsubcategory','flight_boarding_time','meal'],how='left')

In [15]:
part_cols=["flight_number", "flight_boarding_pt","itemcategory","dishsubcategory"]

my_window = Window.partitionBy(part_cols).orderBy('flight_boarding_time')

combined_df = combined_df.withColumn("exp_smooth", lag("exp_smooth",7).over(my_window))  
combined_df = combined_df.withColumn("Doub_exp_smooth", lag("Doub_exp_smooth",7).over(my_window))  
#combined_df = combined_df.select("*", lag("exp_smooth",7).over(my_window).alias("exp_smooth"))  
#combined_df = combined_df.select("*", lag("Doub_exp_smooth",7).over(my_window).alias("Doub_exp_smooth"))  

In [16]:
display(combined_df)

flight_number flight_boarding_pt dishsubcategory flight_boarding_time Meal Adults Africa Americas Asia C Children China Elders Europe F Germany Gulf India Indonesia Iran Italy Japan M Mauritus Middle Aged Northern Africa Oceania Teenagers Thailand U argentinian asian asian / chinese asian / japanese continental / european day dayofweek destination german indian indian ocean / mauritian indonesian italian itemcategory menu_cycle middle eastern middle eastern / gulf middle eastern / iranian month north african pax_count quarter split thai week year meal1 meal2 meal3 meal4 meal5 meal6 meal7 meal8 meal9 meal10 meal11 meal12 meal13 meal14 meal30 meal60 exp_smooth Doub_exp_smooth 773 CPT Poultry 2017-05-02T13:05:00.000+0000 9.0 4.0 7.0 7.0 1.0 null 1.0 null 2.0 5.0 13.0 null null null 2.0 null null null 9.0 null 15.0 null null null null null 0 0 0 0 0 2 1 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 25 2 1 0 18 2017 null null null null null null null null null null null null null null null null null null 773 CPT Poultry 2017-05-23T13:05:00.000+0000 4.0 3.0 7.0 5.0 1.0 null null null 9.0 8.0 5.0 2.0 null null null null null null 18.0 null 11.0 null null null null null 0 0 0 0 0 23 1 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 19 2 1 0 21 2017 9.0 null null null null null null null null null null null null null null null null null 773 CPT Poultry 2017-05-24T13:05:00.000+0000 4.0 4.0 10.0 null null null null null 5.0 6.0 7.0 1.0 1.0 null null null null null 11.0 null 9.0 null null null null null 0 0 0 0 0 24 2 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 20 2 1 0 21 2017 4.0 9.0 null null null null null null null null null null null null null null null null 773 CPT Poultry 2017-05-26T13:05:00.000+0000 4.0 null null null null null null null null 1.0 1.0 null null null null null null null null null 1.0 null null null null null 0 0 0 0 0 26 4 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 16 2 1 0 21 2017 4.0 4.0 9.0 null null null null null null null null null null null null null null null 773 CPT Poultry 2017-05-27T13:05:00.000+0000 8.0 null null 2.0 1.0 null null null 2.0 1.0 3.0 null null null null null 1.0 1.0 4.0 null 5.0 null 1.0 null null null 0 0 0 0 0 27 5 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 27 2 1 0 21 2017 4.0 4.0 4.0 9.0 null null null null null null null null null null null null null null 773 CPT Poultry 2017-05-28T13:05:00.000+0000 7.0 2.0 6.0 2.0 null null null null 7.0 7.0 3.0 null null null null null 1.0 1.0 15.0 null 9.0 null 1.0 null null null 0 0 0 0 0 28 6 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 31 2 1 0 21 2017 8.0 4.0 4.0 4.0 9.0 null null null null null null null null null null null null null 773 CPT Poultry 2017-05-29T13:05:00.000+0000 3.0 4.0 12.0 1.0 null null null null 4.0 4.0 5.0 1.0 null 1.0 null null null null 14.0 null 11.0 null null null null null 0 0 0 0 0 29 0 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 14 2 1 0 22 2017 7.0 8.0 4.0 4.0 4.0 9.0 null null null null null null null null null null null null 773 CPT Poultry 2017-05-31T13:05:00.000+0000 5.0 2.0 7.0 3.0 3.0 null null null 2.0 2.0 4.0 null null null null null null null 11.0 null 11.0 null null null null null 0 0 0 0 0 31 2 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 19 2 1 0 22 2017 3.0 7.0 8.0 4.0 4.0 4.0 9.0 null null null null null null null null null 5.708899944898326 5.309359915800824 773 CPT Poultry 2017-06-01T13:05:00.000+0000 6.0 2.0 5.0 2.0 1.0 null null null 4.0 3.0 4.0 null null null null null 1.0 null 8.0 null 6.0 null null null null null 0 0 0 0 0 1 3 DXB 0 0 0 0 0 Lunch A 0 0 0 6 0 19 2 1 0 22 2017 null null null null null null null null null null null null null null null null 5.238742793886687 4.827351178594855 773 CPT Poultry 2017-06-03T13:05:00.000+0000 4.0 7.0 6.0 null null null null 5.0 8.0 11.0 4.0 1.0 null null null null 1.0 null 20.0 null 9.0 null null null null null 0 0 0 0 0 3 5 DXB 0 0 0 0 0 Lunch A 0 0 0 6 0 25 2 1 0 22 2017 6.0 null null null null null null null null null null null null null null null 5.415706050277876 4.955311856991109 773 CPT Poultry 2017-06-04T13:05:00.000+0000 6.0 9.0 10.0 5.0 1.0 null

In [17]:
# Dummy variables
combined_df_wDummies = combined_df

cat_vars = ['flight_boarding_pt', 'menu_cycle', 'destination','itemcategory', 'dishsubcategory']

for c in cat_vars:
  combined_df_wDummies=combined_df_wDummies.na.fill({c:'Unknown_'+c})
  categories = combined_df_wDummies.select(c).distinct().rdd.flatMap(lambda x : x).collect()
  categories.sort()
  for category in categories:
      function = udf(lambda item: 1 if item == category else 0, IntegerType())
      new_column_name = c+'_'+category
      combined_df_wDummies = combined_df_wDummies.withColumn(new_column_name, function(col(c)))

In [18]:
combined_df = combined_df_wDummies
train = combined_df.filter(col('split') == 1)
test = combined_df.filter(col('split') == 0)

not_indep_vars = ['flight_boarding_time', 'Others', 'Poultry', 'Red Meat', 'Seafood', 'Meal', 
                  #'exp_smooth','Doub_exp_smooth',
                  #'t_7', 't_8', 't_9', 't_10', 't_11', 't_12', 't_13', 't_14', 't_30', 't_60'
                  'Meal1', 'Meal2', 'Meal3', 'Meal4', 'Meal5', 'Meal6',
                  'dishsubcategory_Poultry','dishsubcategory_Seafood','dishsubcategory_Pasta or Vegetarian',
                  'dishsubcategory_Red Meat', 'split', 'date_index']
indep_vars = [e for e in combined_df.columns if e not in not_indep_vars]

target = ['meal']

X_train = train.select(indep_vars)
y_train = train.select(target)

X_test = test.select(indep_vars)
y_test = test.select(target)


In [19]:
display(train)

flight_number flight_boarding_pt dishsubcategory flight_boarding_time Meal Adults Africa Americas Asia C Children China Elders Europe F Germany Gulf India Indonesia Iran Italy Japan M Mauritus Middle Aged Northern Africa Oceania Teenagers Thailand U argentinian asian asian / chinese asian / japanese continental / european day dayofweek destination german indian indian ocean / mauritian indonesian italian itemcategory menu_cycle middle eastern middle eastern / gulf middle eastern / iranian month north african pax_count quarter split thai week year meal1 meal2 meal3 meal4 meal5 meal6 meal7 meal8 meal9 meal10 meal11 meal12 meal13 meal14 meal30 meal60 exp_smooth Doub_exp_smooth flight_boarding_pt_AKL flight_boarding_pt_CDG flight_boarding_pt_CPT flight_boarding_pt_DXB flight_boarding_pt_FRA flight_boarding_pt_JFK flight_boarding_pt_LHR flight_boarding_pt_MEL flight_boarding_pt_MRU flight_boarding_pt_MUC flight_boarding_pt_PEK flight_boarding_pt_PRG flight_boarding_pt_SIN flight_boarding_pt_ZRH menu_cycle_A menu_cycle_B menu_cycle_C menu_cycle_D menu_cycle_FEST2017 menu_cycle_STR menu_cycle_T destination_AUS destination_CDG destination_DXB destination_EUR destination_FRA destination_GER destination_JFK destination_LHR destination_LYS destination_MEL destination_MUC destination_PRG destination_SIN destination_US destination_ZRH itemcategory_Dinner itemcategory_Lunch dishsubcategory_Pasta or Vegetarian dishsubcategory_Poultry dishsubcategory_Red Meat dishsubcategory_Seafood 773 CPT Poultry 2017-05-02T13:05:00.000+0000 9.0 4.0 7.0 7.0 1.0 null 1.0 null 2.0 5.0 13.0 null null null 2.0 null null null 9.0 null 15.0 null null null null null 0 0 0 0 0 2 1 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 25 2 1 0 18 2017 null null null null null null null null null null null null null null null null null null 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2017-05-23T13:05:00.000+0000 4.0 3.0 7.0 5.0 1.0 null null null 9.0 8.0 5.0 2.0 null null null null null null 18.0 null 11.0 null null null null null 0 0 0 0 0 23 1 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 19 2 1 0 21 2017 9.0 null null null null null null null null null null null null null null null null null 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2017-05-24T13:05:00.000+0000 4.0 4.0 10.0 null null null null null 5.0 6.0 7.0 1.0 1.0 null null null null null 11.0 null 9.0 null null null null null 0 0 0 0 0 24 2 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 20 2 1 0 21 2017 4.0 9.0 null null null null null null null null null null null null null null null null 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2017-05-26T13:05:00.000+0000 4.0 null null null null null null null null 1.0 1.0 null null null null null null null null null 1.0 null null null null null 0 0 0 0 0 26 4 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 16 2 1 0 21 2017 4.0 4.0 9.0 null null null null null null null null null null null null null null null 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2017-05-27T13:05:00.000+0000 8.0 null null 2.0 1.0 null null null 2.0 1.0 3.0 null null null null null 1.0 1.0 4.0 null 5.0 null 1.0 null null null 0 0 0 0 0 27 5 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 27 2 1 0 21 2017 4.0 4.0 4.0 9.0 null null null null null null null null null null null null null null 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2017-05-28T13:05:00.000+0000 7.0 2.0 6.0 2.0 null null null null 7.0 7.0 3.0 null null null null null 1.0 1.0 15.0 null 9.0 null 1.0 null null null 0 0 0 0 0 28 6 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 31 2 1 0 21 2017 8.0 4.0 4.0 4.0 9.0 null null null null null null null null null null null null null 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2017-05-29T13:05:00.000+0000 3.0 4.0 12.0 1.0 null null null null 4.0 4.0 5.0 1.0 n

In [20]:
pred_date = "2018-05-01 00:00:00"
# valid_date = pred_date - 30 days
valid_date = "2018-04-01 00:00:00"
# valid_date = max date of historical/MOD data + 1
end_date = "2018-06-15 00:00:00"


temp1 = combined_df
#temp1 = temp1[temp1['flight_boarding_time'] <= "2017-12-01 00:00:00"]

train = temp1.filter(col('flight_boarding_time') < valid_date)
validation = temp1.filter((col('flight_boarding_time') >= valid_date) & (col('flight_boarding_time') < pred_date))
tail15 = temp1.filter((col('flight_boarding_time') >= pred_date) & (col('flight_boarding_time') < end_date) )

test = tail15    

In [21]:
display(test)

flight_number flight_boarding_pt dishsubcategory flight_boarding_time Meal Adults Africa Americas Asia C Children China Elders Europe F Germany Gulf India Indonesia Iran Italy Japan M Mauritus Middle Aged Northern Africa Oceania Teenagers Thailand U argentinian asian asian / chinese asian / japanese continental / european day dayofweek destination german indian indian ocean / mauritian indonesian italian itemcategory menu_cycle middle eastern middle eastern / gulf middle eastern / iranian month north african pax_count quarter split thai week year meal1 meal2 meal3 meal4 meal5 meal6 meal7 meal8 meal9 meal10 meal11 meal12 meal13 meal14 meal30 meal60 exp_smooth Doub_exp_smooth flight_boarding_pt_AKL flight_boarding_pt_CDG flight_boarding_pt_CPT flight_boarding_pt_DXB flight_boarding_pt_FRA flight_boarding_pt_JFK flight_boarding_pt_LHR flight_boarding_pt_MEL flight_boarding_pt_MRU flight_boarding_pt_MUC flight_boarding_pt_PEK flight_boarding_pt_PRG flight_boarding_pt_SIN flight_boarding_pt_ZRH menu_cycle_A menu_cycle_B menu_cycle_C menu_cycle_D menu_cycle_FEST2017 menu_cycle_STR menu_cycle_T destination_AUS destination_CDG destination_DXB destination_EUR destination_FRA destination_GER destination_JFK destination_LHR destination_LYS destination_MEL destination_MUC destination_PRG destination_SIN destination_US destination_ZRH itemcategory_Dinner itemcategory_Lunch dishsubcategory_Pasta or Vegetarian dishsubcategory_Poultry dishsubcategory_Red Meat dishsubcategory_Seafood 773 CPT Poultry 2018-05-01T13:05:00.000+0000 4.0 7.0 11.0 4.0 null null 2.0 null 1.0 null 9.0 null 1.0 5.0 null 9.0 1.0 null 23.0 null 22.0 1.0 null null null null 0 0 0 0 0 1 1 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 19 2 1 0 18 2018 7.0 11.0 10.0 10.0 6.0 7.0 3.0 4.0 5.0 7.0 6.0 5.0 12.0 16.0 10.0 10.0 6.899639757708908 7.564886731836392 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2018-05-03T13:05:00.000+0000 1.0 4.0 8.0 5.0 null null null null 9.0 9.0 12.0 1.0 null 1.0 null null null null 14.0 null 13.0 null null null 2.0 null 0 0 0 0 0 3 3 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 11 2 1 0 18 2018 4.0 7.0 11.0 10.0 10.0 6.0 7.0 3.0 4.0 5.0 7.0 6.0 5.0 12.0 15.0 5.0 6.885302580238681 7.330538715315192 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2018-05-04T13:05:00.000+0000 7.0 2.0 6.0 null 2.0 1.0 1.0 4.0 12.0 8.0 7.0 2.0 null 1.0 null null null null 15.0 null 8.0 null null null null null 0 0 0 0 0 4 4 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 29 2 1 0 18 2018 1.0 4.0 7.0 11.0 10.0 10.0 6.0 7.0 3.0 4.0 5.0 7.0 6.0 5.0 5.0 14.0 7.154631520274291 7.248546465777456 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2018-05-06T13:05:00.000+0000 12.0 4.0 10.0 4.0 2.0 null null 1.0 9.0 7.0 12.0 3.0 null null null null null null 15.0 null 14.0 null null null null null 0 0 0 0 0 6 6 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 37 2 1 0 18 2018 7.0 1.0 4.0 7.0 11.0 10.0 10.0 6.0 7.0 3.0 4.0 5.0 7.0 6.0 13.0 8.0 6.891007451740355 6.658474760629581 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2018-05-08T13:05:00.000+0000 9.0 3.0 9.0 null 1.0 null null null 5.0 8.0 9.0 2.0 null null 5.0 null null null 17.0 null 18.0 null null null 1.0 null 0 0 0 0 0 8 1 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 34 2 1 0 19 2018 12.0 7.0 1.0 4.0 7.0 11.0 10.0 10.0 6.0 7.0 3.0 4.0 5.0 7.0 9.0 8.0 6.732579944844956 6.184458179290742 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773 CPT Poultry 2018-05-09T13:05:00.000+0000 8.0 16.0 23.0 3.0 1.0 null null null null 5.0 14.0 4.0 null 1.0 null 1.0 null null 25.0 null 23.0 null null null null null 0 0 0 0 0 9 2 DXB 0 0 0 0 0 Lunch B 0 0 0 5 0 29 2 1 0 19 2018 9.0 12.0 7.0 1.0 4.0 7.0 11.0 10.0 10.0 6.0 7.0 3.0 4.0 5.0 12.0 8.0 6.694377079822487 5.820533878648179 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 773